In [2]:
reset()
%display latex
Partitions.options.latex="list"
from sage.misc.cachefunc import cached_method, cached_function
from sage.structure.unique_representation import UniqueRepresentation
from itertools import chain, combinations

load("partition_4d.sage")

KT_vars = ['x1','x2','x3','x4','y1','y2','y3','y4','y5','y6','y7','y8','y9',
           'v1','v2','v3','v4','v5','v6','v7','v8','v9']
KT_ring = LaurentPolynomialRing(QQ, KT_vars)

sqrtKT_vars = ['sx1','sx2','sx3','sx4','sy1','sy2','sy3','sy4','sy5','sv1','sv2','sv3','sv4','sv5']
sqrtKT_ring = LaurentPolynomialRing(QQ, KT_vars)

coho_vars = ['t1','t2','t3','t4','m1','m2','m3','m4','m5','m6','m7','m8','m9',
             'w1','w2','w3','w4','w5','w6','w7','w8','w9']
coho_ring = LaurentPolynomialRing(QQ, coho_vars)


rank=1

x1,x2,x3,x4,y1,y2,y3,y4,y5,y6,y7,y8,y9,v1,v2,v3,v4,v5,v6,v7,v8,v9=KT_ring.gens()
#sx1,sx2,sx3,sx4,sy1,sy2,sy3,sy4,sy5,sv1,sv2,sv3,sv4,sv5=sqrtKT_ring.gens()
t1,t2,t3,t4,m1,m2,m3,m4,m5,m6,m7,m8,m9,w1,w2,w3,w4,w5,w6,w7,w8,w9= coho_ring.gens()
b=var('b')
v=[v1,v2,v3,v4,v5,v6,v7,v8,v9]
w=[w1,w2,w3,w4,w5,w6,w7,w8,w9]
y=[y1,y2,y3,y4,y5,y6,y7,y8,y9]

pP4ds = Partitions4d()

def character(p):
    Nx1, Nx2, Nx3, Nx4 = p._Nx1, p._Nx2, p._Nx3, p._Nx4
    return sum(x1**i * x2**j * x3**k * x4**l
           for (i,j,k,l) in p.boxes(Nx1=Nx1, Nx2=Nx2, Nx3=Nx3, Nx4=Nx4))

def dual(f):
    if f in ZZ:
        return f
    R = f.parent()
    g= R.zero()
    for exp, coeff in f.dict().items():
        g+= R({exp.emul(-1): coeff})
    return g

def measure_unsymmetrized(f, inv=True):
    R = f.parent()
    
    if f.parent() is ZZ:
        L = [(ZZ(f), 1)]
    else:
        L = list(f)

    numer, denom = R.one(), R.one()
    for coeff, monomial in L:
        if inv:
            term = 1 - monomial^-1
        else:
            term = 1 - monomial
        if monomial==1:
            term = 0
        if coeff < 0:
            numer *= term ** (-coeff)
        elif coeff > 0:
            denom *= term ** coeff
    return numer / denom

def specialize(f):
    if f in ZZ:
        return f
    return f(x4=x1^-1*x2^-1*x3^-1)

def degn(f,n,b=b):
    g=f.taylor(b,0,n)
    L=g.coefficients(b)
    for i in range(len(L)):
        if L[i][1]==n:
            return L[i][0]
    return 0

def deg0(f):
    if f==0: 
        return 0
    return pretty(degn(f(t1=b*t1,t2=b*t2,t3=b*t3,t4=b*t4,
                         m1=b*m1,m2=b*m2,m3=b*m3,m4=b*m4,m5=b*m5,
                         w1=b*w1,w2=b*w2,w3=b*w3,w4=b*w4,w5=b*w5),0))

def deg0n(f,n):
    if f==0: 
        return 0
    return pretty(degn(f(t1=b*t1,t2=b*t2,t3=b*t3,t4=b*t4,
                         m1=b*m1,m2=b*m2,m3=b*m3,m4=b*m4,m5=b*m5,
                         w1=b*w1,w2=b*w2,w3=b*w3,w4=b*w4,w5=b*w5),n))


def partitions(Sum, K):
    '''computes fixed components of Quot by CC^* action.'''
    total=[]
    def ptn(Sum, K, lst, total):
        if K == 0:
            if Sum == 0:
                total+=[lst]
            return
        for i in range(0, min(Sum + 1, Sum + 1)):
            ptn(Sum - i, K - 1, lst + [i],total)
    ptn(Sum,K,[],total)
    return total


def fixed_locus(n, N):
    total=[]
    ptns=partitions(n,N)
    for j in range(len(ptns)):
        ptn=ptns[j]
        lst=[]
        for i in range(N):
            lst+=[list(pP4ds.with_num_boxes(ptn[i]))]
        total+=[p for p in itertools.product(*lst)]
    return total


def sign(Z):
    s=1
    for i in range(len(Z)):
        s=s*Z[i].sign()
    return s
        

def Nvir(Z):
    total=0
    for i in range(len(Z)):
        for j in range(len(Z)):
            Qj=character(Z[j])
            Qiinv=dual(character(Z[i]))
            total+=(Qj+Qiinv/(x1*x2*x3*x4)-Qj*Qiinv*(1-x1)*(1-x2)*(1-x3)*(1-x4)/(x1*x2*x3*x4))*(y[j]/y[i])
    return total

def sqrtNvir(Z,check=False):
    sqrtN=0
    for i in range(len(Z)):
        for j in range(len(Z)):
            Qj=specialize(character(Z[j]))
            Qi=specialize(character(Z[i]))
            Qiinv=dual(Qi)
            sqrtN+=(Qj-(1-x1^-1)*(1-x2^-1)*(1-x3^-1)*Qiinv*Qj)*(y[j]/y[i])
        

    if check:
        if sqrtN+dual(sqrtN)!=specialize(Nvir(Z)):
            print(sqrtN)
            print(specialize(Nvir(Z)))
            raise ValueError("something went wrong in computation"+Z.__str__())

    return sqrtN+x1^-1*x2^-1+x3^-1*x2^-1+x1^-1*x3^-1

def determinant(f):
    if f in ZZ:
        return 1
    else:
        return prod((mon)^coeff for coeff, mon in f)
    
def from_monomial(m):
    R = m.parent()
    if R== KT_ring:
        return sum(m.degree(R.gen(i)) * coho_ring.gen(i) for i in range(len(coho_vars)))
    elif R==sqrtKT_ring:
        return sum((1/2)*m.degree(R.gen(i)) * coho_ring.gen(i) for i in range(len(coho_vars)))
    else:
        raise NotImplementedError("%s" % R)

def top_chern(f):
    numer, denom = [], []
    for coeff, mon in list(f):
        wt = from_monomial(mon)
        if coeff > 0:
            numer += (coeff) * [wt]
        elif coeff < 0:
            denom += (-coeff) * [wt]
    return coho_ring.fraction_field()(prod(numer) / prod(denom))


def total_chern_quot(Z, rank):
    total=1
    for i in range(len(Z)):
        Q = specialize(character(Z[i]))*(y[i])
        roots = []
        for coeff, mon in list(Q):
            wt = from_monomial(mon)
            for i in range(rank):
                roots += (coeff) * [wt+w[i]]
        total *= prod((1+r) for r in roots)
    return total


def Chern_Num_quot(n,N,r):
    total=0
    for Z in fixed_locus(n,N):
        add=sign(Z)*top_chern(-sqrtNvir(Z))*total_chern_quot(Z,r)
        total+=add
    return total

def cut_off_n(f,n):
    if f in ZZ:
        return f
    D=f.dict()
    for exp,coeff in f.dict().items():
        if sum(exp)>n:
            del D[exp]
    return coho_ring(D)

def restrict(f,n):
    D=f.dict()
    for exp,coeff in f.dict().items():
        if sum(exp)!=n:
            del D[exp]
    return coho_ring(D)

def total_segre_quot(Z, rank,n):
    total=1
    for i in range(len(Z)):
        Q = specialize(character(Z[i]))*(y[i])
        roots = []
        for coeff, mon in list(Q):
            wt = from_monomial(mon)
            for i in range(rank):
                roots += (coeff) * [wt+w[i]]
        total*=prod(1/(1+r) for r in roots)
    return total

def total_segre_quot_fast(Z, rank,n,N):
    total=1
    for i in range(len(Z)):
        Q = specialize(character(Z[i]))*(y[i])
        roots = []
        for coeff, mon in list(Q):
            wt = from_monomial(mon)
            for i in range(rank):
                roots += (coeff) * [wt+w[i]]
        for r in roots:
            total=cut_off_n(total*(1+sum((-1)^(k+1)*r^(k+1) for k in range(n*N))),n*N)
    return restrict(total,n*N)

def Segre_Num_quot_fast(n,N,r):
    total=0
    maxcounter=len(fixed_locus(n,N))
    counter=0
    for Z in fixed_locus(n,N):
        add=sign(Z)*top_chern(-sqrtNvir(Z))*total_segre_quot_fast(Z,r,n,N)
        total+=add
        counter+=1
        print("added"+str(counter)+"/"+str(maxcounter))
    return total

def Segre_Num_quot(n,N,r):
    total=0
    maxcounter=len(fixed_locus(n,N))
    counter=0
    for Z in fixed_locus(n,N):
        add=sign(Z)*top_chern(-sqrtNvir(Z))*total_segre_quot(Z,r,n)
        total+=add
        counter+=1
        print("added"+str(counter)+"/"+str(maxcounter))
    return total

def Segre_Num_quot_sym(n,N,r):
    total=0
    maxcounter=len(fixed_locus(n,r))
    counter=0
    for Z in fixed_locus(n,r):
        add=sign(Z)*symmetrize(top_chern(-sqrtNvir(Z)))*symmetrize(total_segre_quot(Z,N,n))
        total+=add
        counter+=1
        print("added"+str(counter)+"/"+str(maxcounter))
    return total

def determinant_quot(Z,n, rank):
    det=1
    for i in range(len(Z)):
        Q = specialize(character(Z[i]))*(y[i])
        det *= determinant(Q)
    return (det^rank)*((prod(v[i] for i in range(rank)))^n)

def determinant_fast(f,n):
    if f in ZZ:
        return 1
    else:
        total=1
        for coeff,mon in f:
            term=1+sum((coeff*from_monomial(mon))^(k+1)/factorial(k+1) for k in range(n))
            total=cut_off_n(total*term,n)
        return total

def determinant_quot_fast(Z,n, rank,N):
    det=1
    v_1=1
    v_2=1
    Q_2=1
    for i in range(rank):
        v_1=cut_off_n(v_1*(1+sum((w[i])^(k+1)/factorial(k+1) for k in range(n*N))),n*N)
    for i in range(n):
        v_2=cut_off_n(v_2*v_1,n*N)
    for i in range(len(Z)):
        Q = specialize(character(Z[i]))*(y[i])
        det = cut_off_n(det* determinant_fast(Q,n*N),n*N)
    for i in range(rank):
        Q_2=cut_off_n(Q_2*det,n*N)
    return cut_off_n(Q_2*v_2,n*N)

def todd_class_fast(f,n):
    R = f.parent()
    total=1
    if f.parent() is ZZ:
        L = [(ZZ(f), 1)]
    else:
        L = list(f)
    for coeff, mon in L:
        t=1
        if mon==1:
            term = 0
        if coeff < 0:
            term = 1+sum((-1)^(k+1)*(from_monomial(mon))^(k+1)/factorial(k+2) for k in range(n))
            for i in range(-coeff):
                t=cut_off_n(t*term,n)
        elif coeff > 0:
            term = 1+sum(bernoulli_polynomial(1, k+1)*(from_monomial(mon))^(k+1)/factorial(k+1) for k in range(n))
            for i in range(coeff):
                t=cut_off_n(t*term,n)
        total=cut_off_n(total*t,n)
    return total

def Verlinde_Num_quot_fast(n,N, r):
    total=0
    maxcounter=len(fixed_locus(n,N))
    counter=0
    for Z in fixed_locus(n,N):
        add=sign(Z)*top_chern(-sqrtNvir(Z))*\
            restrict(todd_class_fast(sqrtNvir(Z),n*N)*determinant_quot_fast(Z,n,r,N),n*N)
        total+=add
        counter+=1
        print("added"+str(counter)+"/"+str(maxcounter))
    return total

def Verlinde_Num_quot(n,N, r):
    total=0
    maxcounter=len(fixed_locus(n,N))
    counter=0
    for Z in fixed_locus(n,N):
        add=sign(Z)*measure_unsymmetrized(sqrtNvir(Z))*\
            determinant_quot(Z,n,r)
        total+=add
        counter+=1
        print("added"+str(counter)+"/"+str(maxcounter))
    return total

def Verlinde_Num_quot_inv(n,N, r):
    total=0
    for Z in fixed_locus(n,N):
        add=sign(Z)*measure_unsymmetrized(sqrtNvir(Z))*\
            (1/determinant_quot(Z,n,r))
        total+=add
    return total

def set_exp(f,n):
    g=cut_off_n(f(x1=1+sum(t1^(k+1)/factorial(k+1) for k in range(n)),
        x2=1+sum(t2^(k+1)/factorial(k+1) for k in range(n)),
        x3=1+sum(t3^(k+1)/factorial(k+1) for k in range(n)),
        x4=1+sum(t4^(k+1)/factorial(k+1) for k in range(n)),
        y1=1+sum(m1^(k+1)/factorial(k+1) for k in range(n)),
        y2=1+sum(m2^(k+1)/factorial(k+1) for k in range(n)),
        y3=1+sum(m3^(k+1)/factorial(k+1) for k in range(n)),
        y4=1+sum(m4^(k+1)/factorial(k+1) for k in range(n)),
        y5=1+sum(m5^(k+1)/factorial(k+1) for k in range(n)),
        v1=1+sum(w1^(k+1)/factorial(k+1) for k in range(n)),
        v2=1+sum(w2^(k+1)/factorial(k+1) for k in range(n)),
        v3=1+sum(w3^(k+1)/factorial(k+1) for k in range(n)),
        v4=1+sum(w4^(k+1)/factorial(k+1) for k in range(n)),
        v5=1+sum(w5^(k+1)/factorial(k+1) for k in range(n))),n)
    return g

def invert_exp(f):
    g=f(t1=-t1,t2=-t2,t3=-t3,t4=-t4,
                  m1=-m1,m2=-m2,m3=-m3,m4=-m4,m5=-m5,
                  w1=-w1,w2=-w2,w3=-w3,w4=-w4,w5=-w5)
    return g

def symmetrize(f):
    if f in ZZ:
        return f
    return f(m1=w1,m2=w2,m3=w3,m4=w4,m5=w5,w1=m1,w2=m2,w3=m3,w4=m4,w5=m5)

def symmetrizeK(f):
    if f in ZZ:
        return f
    return f(y1=v1,y2=v2,y3=v3,y4=v4,y5=v5,v1=y1,v2=y2,v3=y3,v4=y4,v5=y5)


def check_sym(nlimit):
    with open("symmetry4d-segre-checked.txt") as f:
        lines_segre = f.read().splitlines()
    for n in range(1,nlimit+1):
        N,r=[1,3]
        print("checking segre sym: n="+str(n)+", N="+str(N)+", r="+str(r))
        if str(n)+','+str(N)+','+str(r) in lines_segre:
            print("n="+str(n)+", N="+str(N)+", r="+str(r)+" already checked")
        else:
            print("computing S1")
            A=Segre_Num_quot(n,N,r)
            print("computing S2")
            B=Segre_Num_quot_sym(n,N,r)
            A1=A.numerator()
            B1=B.numerator()
            A2=A.denominator()
            B2=B.denominator()
            print("computing diff")
            diff=(A1.lc()/A2.lc())/(B1.lc()/B2.lc())
            A1=A1*(B1.lc()/A1.lc())
            A2=A2*(B2.lc()/A2.lc())
            if diff==(-1)^(n*(r+N)) and A1==B1 and A2==B2:
                writeline("symmetry4d-segre-checked.txt",str(n)+','+str(N)+','+str(r))
                print("checked")
            else:
                print("failed")
                    
                
def clear_all_files():
    open('SV4d-checked.txt', 'w').close()
    open('symmetry4d-segre-checked.txt', 'w').close()
    open('symmetry4d-Verlinde-checked.txt', 'w').close()
    
    
def SV_check_fast(nlimit, rlimit):
    with open("SV4d-checked.txt") as f:
        lines = f.read().splitlines()
    for n in range(1,nlimit+1):
        for N in range(1,rlimit+1):
            for r in range(1,rlimit+1):
                print("n="+str(n)+", N="+str(N)+", r="+str(r))
                if str(n)+','+str(N)+','+str(r) in lines:
                    print("n="+str(n)+", N="+str(N)+", r="+str(r)+" already checked")
                    continue
                print("computing S1")
                S1=Segre_Num_quot_fast(n,N,r)
                print("computing V1")
                V1=Verlinde_Num_quot_fast(n,N,r)
                print("computing diff")
                diff= S1-(-1)^(N*n)*V1
                check1=false
                check2=false
                check3=false
                if diff.numerator()==0:
                    check1=true
                    check2=true
                    check3=true
                else:
                    for f,e in list(diff.numerator().factor()):
                        if e>=2:
                            if f==t1+t2:
                                check1=true
                            if f==t2+t3:
                                check2=true
                            if f==t1+t3:
                                check3=true
                if check1 and check2 and check3:
                    writeline("SV4d-checked.txt",str(n)+','+str(N)+','+str(r))
                    print("checked")
                else:
                    print("failed")
                    

def writeline(file,s):
    g = open(file, "a")
    g.write(s+"\n")
    g.close()

In [3]:
A=Segre_Num_quot_sym(3,1,3)
A1=A.numerator()
A2=A.denominator()

added1/55
added2/55
added3/55
added4/55
added5/55


KeyboardInterrupt: 

In [ ]:
writeline("Segre-331-num.txt",A1.__str__())
writeline("Segre-331-den.txt",A2.__str__())

In [46]:
A=Segre_Num_quot(1,1,2)
B=Segre_Num_quot_sym(1,1,2)
A1=A.numerator()
B1=B.numerator()
A2=A.denominator()
B2=B.denominator()
A1.lc()/A2.lc()==B1.lc()/B2.lc()
A1=A1*(B1.lc()/A1.lc())
A2=A2*(B2.lc()/A2.lc())

added1/1
added1/2
added2/2


True

In [37]:
print(A1)

t1^2*t2 + t1*t2^2 + t1^2*t3 + 2*t1*t2*t3 + t2^2*t3 + t1*t3^2 + t2*t3^2


In [38]:
print(B1)

t1^2*t2 + t1*t2^2 + t1^2*t3 + 2*t1*t2*t3 + t2^2*t3 + t1*t3^2 + t2*t3^2


In [39]:
print(A2)

-t1^2*t2*t3*m1*m2 - t1*t2^2*t3*m1*m2 - t1*t2*t3^2*m1*m2 - t1^2*t2*t3*m1*w1 - t1*t2^2*t3*m1*w1 - t1*t2*t3^2*m1*w1 - t1^2*t2*t3*m2*w1 - t1*t2^2*t3*m2*w1 - t1*t2*t3^2*m2*w1 - t1^2*t2*t3*w1^2 - t1*t2^2*t3*w1^2 - t1*t2*t3^2*w1^2 - t1^2*t2*t3*m1 - t1*t2^2*t3*m1 - t1*t2*t3^2*m1 - t1^2*t2*t3*m2 - t1*t2^2*t3*m2 - t1*t2*t3^2*m2 - 2*t1^2*t2*t3*w1 - 2*t1*t2^2*t3*w1 - 2*t1*t2*t3^2*w1 - t1^2*t2*t3 - t1*t2^2*t3 - t1*t2*t3^2


In [40]:
print(B2)

-t1^2*t2*t3*m1^2 - t1*t2^2*t3*m1^2 - t1*t2*t3^2*m1^2 - t1^2*t2*t3*m1*w1 - t1*t2^2*t3*m1*w1 - t1*t2*t3^2*m1*w1 - t1^2*t2*t3*m1*w2 - t1*t2^2*t3*m1*w2 - t1*t2*t3^2*m1*w2 - t1^2*t2*t3*w1*w2 - t1*t2^2*t3*w1*w2 - t1*t2*t3^2*w1*w2 - 2*t1^2*t2*t3*m1 - 2*t1*t2^2*t3*m1 - 2*t1*t2*t3^2*m1 - t1^2*t2*t3*w1 - t1*t2^2*t3*w1 - t1*t2*t3^2*w1 - t1^2*t2*t3*w2 - t1*t2^2*t3*w2 - t1*t2*t3^2*w2 - t1^2*t2*t3 - t1*t2^2*t3 - t1*t2*t3^2


In [ ]:
A2=Segre_Num_quot_sym(2,2,1).numerator()

In [6]:
(Segre_Num_quot_sym(2,2,1)*16).__str__()

added1/4
added2/4
added3/4
added4/4


'(-128*t1^8*t2^4 - 512*t1^7*t2^5 - 768*t1^6*t2^6 - 512*t1^5*t2^7 - 128*t1^4*t2^8 - 512*t1^8*t2^3*t3 - 2560*t1^7*t2^4*t3 - 5120*t1^6*t2^5*t3 - 5120*t1^5*t2^6*t3 - 2560*t1^4*t2^7*t3 - 512*t1^3*t2^8*t3 - 768*t1^8*t2^2*t3^2 - 5120*t1^7*t2^3*t3^2 - 13568*t1^6*t2^4*t3^2 - 18432*t1^5*t2^5*t3^2 - 13568*t1^4*t2^6*t3^2 - 5120*t1^3*t2^7*t3^2 - 768*t1^2*t2^8*t3^2 - 512*t1^8*t2*t3^3 - 5120*t1^7*t2^2*t3^3 - 18432*t1^6*t2^3*t3^3 - 33280*t1^5*t2^4*t3^3 - 33280*t1^4*t2^5*t3^3 - 18432*t1^3*t2^6*t3^3 - 5120*t1^2*t2^7*t3^3 - 512*t1*t2^8*t3^3 - 128*t1^8*t3^4 - 2560*t1^7*t2*t3^4 - 13568*t1^6*t2^2*t3^4 - 33280*t1^5*t2^3*t3^4 - 44288*t1^4*t2^4*t3^4 - 33280*t1^3*t2^5*t3^4 - 13568*t1^2*t2^6*t3^4 - 2560*t1*t2^7*t3^4 - 128*t2^8*t3^4 - 512*t1^7*t3^5 - 5120*t1^6*t2*t3^5 - 18432*t1^5*t2^2*t3^5 - 33280*t1^4*t2^3*t3^5 - 33280*t1^3*t2^4*t3^5 - 18432*t1^2*t2^5*t3^5 - 5120*t1*t2^6*t3^5 - 512*t2^7*t3^5 - 768*t1^6*t3^6 - 5120*t1^5*t2*t3^6 - 13568*t1^4*t2^2*t3^6 - 18432*t1^3*t2^3*t3^6 - 13568*t1^2*t2^4*t3^6 - 5120*t1*t2^5*t3^6 - 768*t2^6*t3^6 - 512*t1^5*t3^7 - 2560*t1^4*t2*t3^7 - 5120*t1^3*t2^2*t3^7 - 5120*t1^2*t2^3*t3^7 - 2560*t1*t2^4*t3^7 - 512*t2^5*t3^7 - 128*t1^4*t3^8 - 512*t1^3*t2*t3^8 - 768*t1^2*t2^2*t3^8 - 512*t1*t2^3*t3^8 - 128*t2^4*t3^8 - 128*t1^8*t2^3*m1 - 512*t1^7*t2^4*m1 - 896*t1^6*t2^5*m1 - 896*t1^5*t2^6*m1 - 512*t1^4*t2^7*m1 - 128*t1^3*t2^8*m1 - 512*t1^8*t2^2*t3*m1 - 2560*t1^7*t2^3*t3*m1 - 5760*t1^6*t2^4*t3*m1 - 7424*t1^5*t2^5*t3*m1 - 5760*t1^4*t2^6*t3*m1 - 2560*t1^3*t2^7*t3*m1 - 512*t1^2*t2^8*t3*m1 - 512*t1^8*t2*t3^2*m1 - 4096*t1^7*t2^2*t3^2*m1 - 13312*t1^6*t2^3*t3^2*m1 - 23168*t1^5*t2^4*t3^2*m1 - 23168*t1^4*t2^5*t3^2*m1 - 13312*t1^3*t2^6*t3^2*m1 - 4096*t1^2*t2^7*t3^2*m1 - 512*t1*t2^8*t3^2*m1 - 128*t1^8*t3^3*m1 - 2560*t1^7*t2*t3^3*m1 - 13312*t1^6*t2^2*t3^3*m1 - 33280*t1^5*t2^3*t3^3*m1 - 44800*t1^4*t2^4*t3^3*m1 - 33280*t1^3*t2^5*t3^3*m1 - 13312*t1^2*t2^6*t3^3*m1 - 2560*t1*t2^7*t3^3*m1 - 128*t2^8*t3^3*m1 - 512*t1^7*t3^4*m1 - 5760*t1^6*t2*t3^4*m1 - 23168*t1^5*t2^2*t3^4*m1 - 44800*t1^4*t2^3*t3^4*m1 - 44800*t1^3*t2^4*t3^4*m1 - 23168*t1^2*t2^5*t3^4*m1 - 5760*t1*t2^6*t3^4*m1 - 512*t2^7*t3^4*m1 - 896*t1^6*t3^5*m1 - 7424*t1^5*t2*t3^5*m1 - 23168*t1^4*t2^2*t3^5*m1 - 33280*t1^3*t2^3*t3^5*m1 - 23168*t1^2*t2^4*t3^5*m1 - 7424*t1*t2^5*t3^5*m1 - 896*t2^6*t3^5*m1 - 896*t1^5*t3^6*m1 - 5760*t1^4*t2*t3^6*m1 - 13312*t1^3*t2^2*t3^6*m1 - 13312*t1^2*t2^3*t3^6*m1 - 5760*t1*t2^4*t3^6*m1 - 896*t2^5*t3^6*m1 - 512*t1^4*t3^7*m1 - 2560*t1^3*t2*t3^7*m1 - 4096*t1^2*t2^2*t3^7*m1 - 2560*t1*t2^3*t3^7*m1 - 512*t2^4*t3^7*m1 - 128*t1^3*t3^8*m1 - 512*t1^2*t2*t3^8*m1 - 512*t1*t2^2*t3^8*m1 - 128*t2^3*t3^8*m1 - 128*t1^6*t2^3*t3*m1^2 - 384*t1^5*t2^4*t3*m1^2 - 384*t1^4*t2^5*t3*m1^2 - 128*t1^3*t2^6*t3*m1^2 - 256*t1^6*t2^2*t3^2*m1^2 - 1152*t1^5*t2^3*t3^2*m1^2 - 1792*t1^4*t2^4*t3^2*m1^2 - 1152*t1^3*t2^5*t3^2*m1^2 - 256*t1^2*t2^6*t3^2*m1^2 - 128*t1^6*t2*t3^3*m1^2 - 1152*t1^5*t2^2*t3^3*m1^2 - 2816*t1^4*t2^3*t3^3*m1^2 - 2816*t1^3*t2^4*t3^3*m1^2 - 1152*t1^2*t2^5*t3^3*m1^2 - 128*t1*t2^6*t3^3*m1^2 - 384*t1^5*t2*t3^4*m1^2 - 1792*t1^4*t2^2*t3^4*m1^2 - 2816*t1^3*t2^3*t3^4*m1^2 - 1792*t1^2*t2^4*t3^4*m1^2 - 384*t1*t2^5*t3^4*m1^2 - 384*t1^4*t2*t3^5*m1^2 - 1152*t1^3*t2^2*t3^5*m1^2 - 1152*t1^2*t2^3*t3^5*m1^2 - 384*t1*t2^4*t3^5*m1^2 - 128*t1^3*t2*t3^6*m1^2 - 256*t1^2*t2^2*t3^6*m1^2 - 128*t1*t2^3*t3^6*m1^2 + 128*t1^6*t2^3*m1^3 + 384*t1^5*t2^4*m1^3 + 384*t1^4*t2^5*m1^3 + 128*t1^3*t2^6*m1^3 + 512*t1^6*t2^2*t3*m1^3 + 1920*t1^5*t2^3*t3*m1^3 + 2816*t1^4*t2^4*t3*m1^3 + 1920*t1^3*t2^5*t3*m1^3 + 512*t1^2*t2^6*t3*m1^3 + 512*t1^6*t2*t3^2*m1^3 + 3072*t1^5*t2^2*t3^2*m1^3 + 6528*t1^4*t2^3*t3^2*m1^3 + 6528*t1^3*t2^4*t3^2*m1^3 + 3072*t1^2*t2^5*t3^2*m1^3 + 512*t1*t2^6*t3^2*m1^3 + 128*t1^6*t3^3*m1^3 + 1920*t1^5*t2*t3^3*m1^3 + 6528*t1^4*t2^2*t3^3*m1^3 + 9472*t1^3*t2^3*t3^3*m1^3 + 6528*t1^2*t2^4*t3^3*m1^3 + 1920*t1*t2^5*t3^3*m1^3 + 128*t2^6*t3^3*m1^3 + 384*t1^5*t3^4*m1^3 + 2816*t1^4*t2*t3^4*m1^3 + 6528*t1^3*t2^2*t3^4*m1^3 + 6528*t1^2*t2^3*t3^4*m1^3 + 2816*t1*t2^4*t3^4*m1^3 + 384*t2^5*t3^4*m1^3 + 384*t1^4*t3^5*m1^3 + 1920*t1^3*t2*t3^

In [26]:
S1=Segre_Num_quot(3,1,2)
S1.numerator().__str__()

added1/10
added2/10
added3/10
added4/10
added5/10
added6/10
added7/10
added8/10
added9/10
added10/10


'221184*t1^14*t2^7 + 1548288*t1^13*t2^8 + 4644864*t1^12*t2^9 + 7741440*t1^11*t2^10 + 7741440*t1^10*t2^11 + 4644864*t1^9*t2^12 + 1548288*t1^8*t2^13 + 221184*t1^7*t2^14 + 1990656*t1^14*t2^6*t3 + 15482880*t1^13*t2^7*t3 + 53084160*t1^12*t2^8*t3 + 104841216*t1^11*t2^9*t3 + 130498560*t1^10*t2^10*t3 + 104841216*t1^9*t2^11*t3 + 53084160*t1^8*t2^12*t3 + 15482880*t1^7*t2^13*t3 + 1990656*t1^6*t2^14*t3 + 7962624*t1^14*t2^5*t3^2 + 69672960*t1^13*t2^6*t3^2 + 273383424*t1^12*t2^7*t3^2 + 630374400*t1^11*t2^8*t3^2 + 940253184*t1^10*t2^9*t3^2 + 940253184*t1^9*t2^10*t3^2 + 630374400*t1^8*t2^11*t3^2 + 273383424*t1^7*t2^12*t3^2 + 69672960*t1^6*t2^13*t3^2 + 7962624*t1^5*t2^14*t3^2 + 15925248*t1^14*t2^4*t3^3 + 167215104*t1^13*t2^5*t3^3 + 782327808*t1^12*t2^6*t3^3 + 2147696640*t1^11*t2^7*t3^3 + 3827146752*t1^10*t2^8*t3^3 + 4620976128*t1^9*t2^9*t3^3 + 3827146752*t1^8*t2^10*t3^3 + 2147696640*t1^7*t2^11*t3^3 + 782327808*t1^6*t2^12*t3^3 + 167215104*t1^5*t2^13*t3^3 + 15925248*t1^4*t2^14*t3^3 + 15925248*t1^14*t2^3*t3^4 + 222953472*t1^13*t2^4*t3^4 + 1313832960*t1^12*t2^5*t3^4 + 4425228288*t1^11*t2^6*t3^4 + 9544974336*t1^10*t2^7*t3^4 + 13874208768*t1^9*t2^8*t3^4 + 13874208768*t1^8*t2^9*t3^4 + 9544974336*t1^7*t2^10*t3^4 + 4425228288*t1^6*t2^11*t3^4 + 1313832960*t1^5*t2^12*t3^4 + 222953472*t1^4*t2^13*t3^4 + 15925248*t1^3*t2^14*t3^4 + 7962624*t1^14*t2^2*t3^5 + 167215104*t1^13*t2^3*t3^5 + 1313832960*t1^12*t2^4*t3^5 + 5621612544*t1^11*t2^5*t3^5 + 14991630336*t1^10*t2^6*t3^5 + 26498285568*t1^9*t2^7*t3^5 + 31947374592*t1^8*t2^8*t3^5 + 26498285568*t1^7*t2^9*t3^5 + 14991630336*t1^6*t2^10*t3^5 + 5621612544*t1^5*t2^11*t3^5 + 1313832960*t1^4*t2^12*t3^5 + 167215104*t1^3*t2^13*t3^5 + 7962624*t1^2*t2^14*t3^5 + 1990656*t1^14*t2*t3^6 + 69672960*t1^13*t2^2*t3^6 + 782327808*t1^12*t2^3*t3^6 + 4425228288*t1^11*t2^4*t3^6 + 14991630336*t1^10*t2^5*t3^6 + 32809992192*t1^9*t2^6*t3^6 + 48147554304*t1^8*t2^7*t3^6 + 48147554304*t1^7*t2^8*t3^6 + 32809992192*t1^6*t2^9*t3^6 + 14991630336*t1^5*t2^10*t3^6 + 4425228288*t1^4*t2^11*t3^6 + 782327808*t1^3*t2^12*t3^6 + 69672960*t1^2*t2^13*t3^6 + 1990656*t1*t2^14*t3^6 + 221184*t1^14*t3^7 + 15482880*t1^13*t2*t3^7 + 273383424*t1^12*t2^2*t3^7 + 2147696640*t1^11*t2^3*t3^7 + 9544974336*t1^10*t2^4*t3^7 + 26498285568*t1^9*t2^5*t3^7 + 48147554304*t1^8*t2^6*t3^7 + 58609336320*t1^7*t2^7*t3^7 + 48147554304*t1^6*t2^8*t3^7 + 26498285568*t1^5*t2^9*t3^7 + 9544974336*t1^4*t2^10*t3^7 + 2147696640*t1^3*t2^11*t3^7 + 273383424*t1^2*t2^12*t3^7 + 15482880*t1*t2^13*t3^7 + 221184*t2^14*t3^7 + 1548288*t1^13*t3^8 + 53084160*t1^12*t2*t3^8 + 630374400*t1^11*t2^2*t3^8 + 3827146752*t1^10*t2^3*t3^8 + 13874208768*t1^9*t2^4*t3^8 + 31947374592*t1^8*t2^5*t3^8 + 48147554304*t1^7*t2^6*t3^8 + 48147554304*t1^6*t2^7*t3^8 + 31947374592*t1^5*t2^8*t3^8 + 13874208768*t1^4*t2^9*t3^8 + 3827146752*t1^3*t2^10*t3^8 + 630374400*t1^2*t2^11*t3^8 + 53084160*t1*t2^12*t3^8 + 1548288*t2^13*t3^8 + 4644864*t1^12*t3^9 + 104841216*t1^11*t2*t3^9 + 940253184*t1^10*t2^2*t3^9 + 4620976128*t1^9*t2^3*t3^9 + 13874208768*t1^8*t2^4*t3^9 + 26498285568*t1^7*t2^5*t3^9 + 32809992192*t1^6*t2^6*t3^9 + 26498285568*t1^5*t2^7*t3^9 + 13874208768*t1^4*t2^8*t3^9 + 4620976128*t1^3*t2^9*t3^9 + 940253184*t1^2*t2^10*t3^9 + 104841216*t1*t2^11*t3^9 + 4644864*t2^12*t3^9 + 7741440*t1^11*t3^10 + 130498560*t1^10*t2*t3^10 + 940253184*t1^9*t2^2*t3^10 + 3827146752*t1^8*t2^3*t3^10 + 9544974336*t1^7*t2^4*t3^10 + 14991630336*t1^6*t2^5*t3^10 + 14991630336*t1^5*t2^6*t3^10 + 9544974336*t1^4*t2^7*t3^10 + 3827146752*t1^3*t2^8*t3^10 + 940253184*t1^2*t2^9*t3^10 + 130498560*t1*t2^10*t3^10 + 7741440*t2^11*t3^10 + 7741440*t1^10*t3^11 + 104841216*t1^9*t2*t3^11 + 630374400*t1^8*t2^2*t3^11 + 2147696640*t1^7*t2^3*t3^11 + 4425228288*t1^6*t2^4*t3^11 + 5621612544*t1^5*t2^5*t3^11 + 4425228288*t1^4*t2^6*t3^11 + 2147696640*t1^3*t2^7*t3^11 + 630374400*t1^2*t2^8*t3^11 + 104841216*t1*t2^9*t3^11 + 7741440*t2^10*t3^11 + 4644864*t1^9*t3^12 + 53084160*t1^8*t2*t3^12 + 273383424*t1^7*t2^2*t3^12 + 782327808*t1^6*t2^3*t3^12 + 1313832960*t1^5*t2^4*t3^12 + 1313832960*t1^4*t2^

In [32]:
S2=Segre_Num_quot(3,2,1)

added1/28
added2/28
added3/28
added4/28
added5/28
added6/28
added7/28
added8/28
added9/28
added10/28
added11/28
added12/28
added13/28
added14/28
added15/28
added16/28
added17/28
added18/28
added19/28
added20/28
added21/28
added22/28
added23/28
added24/28
added25/28
added26/28
added27/28
added28/28


In [28]:
writeline("segre-out-1.txt",S1.numerator().__str__())

In [34]:
Astr=S2.numerator().__str__()
print("ok")
Astr=Astr.replace("w","f")
print("ok")
Astr=Astr.replace("m","w")
print("ok")
Astr=Astr.replace("f","m")
print("ok")
writeline("segre-out-2.txt",Astr)

ok
ok
ok
ok


In [30]:
writeline("segre-out-3.txt",S1.denominator().__str__())

In [37]:
open('segre-out-4.txt', 'w').close()
Bstr=S2.denominator().__str__()
print("ok")
Bstr=Bstr.replace("w","f")
print("ok")
Bstr=Bstr.replace("m","w")
print("ok")
Bstr=Bstr.replace("f","m")
print("ok")
writeline("segre-out-4.txt",Bstr)

ok
ok
ok
ok


In [1]:
with open("segre-out-2.txt") as f:
    lines = f.read().splitlines()
A=lines[0]
span = 2
words1 = A.split(" ")
B= [" ".join(words1[i:i+span]) for i in range(1, len(words1), span)]

In [49]:
with open("segre-out-1.txt") as f:
    lines = f.read().splitlines()
C=lines[0]
span = 2
words2 = C.split(" ")
D= [" ".join(words2[i:i+span]) for i in range(1, len(words2), span)]

In [ ]:
BB={SR(term)/-5308416 for term in B}

In [ ]:
len(BB)

In [55]:
BB<=DD

True

In [53]:
DD={SR(term) for term in D}

In [56]:
DD<=BB

True

In [60]:
with open("segre-out-3.txt") as f:
    lines = f.read().splitlines()
A=lines[0]
span = 2
words1 = A.split(" ")
B= [" ".join(words1[i:i+span]) for i in range(1, len(words1), span)]

In [61]:
with open("segre-out-4.txt") as f:
    lines = f.read().splitlines()
C=lines[0]
span = 2
words2 = C.split(" ")
D= [" ".join(words2[i:i+span]) for i in range(1, len(words2), span)]

In [62]:
AA={SR(term)/5308416 for term in D}

In [63]:
CC={SR(term) for term in B}

In [64]:
AA<=CC

True

In [65]:
CC<=AA

True

---------------------------------

In [14]:
check_sym(2)

checking segre sym: n=1, N=1, r=3
computing S1
added1/1
computing S2
added1/3
added2/3
added3/3
computing diff
checked
checking segre sym: n=2, N=1, r=3
computing S1
added1/4
added2/4
added3/4
added4/4
computing S2
added1/15
added2/15
added3/15
added4/15
added5/15
added6/15
added7/15
added8/15
added9/15
added10/15
added11/15
added12/15
added13/15
added14/15
added15/15
computing diff


KeyboardInterrupt: 

In [ ]:
SV_check_fast(2,4)

n=1, N=1, r=1
n=1, N=1, r=1 already checked
n=1, N=1, r=2
n=1, N=1, r=2 already checked
n=1, N=1, r=3
n=1, N=1, r=3 already checked
n=1, N=1, r=4
computing S1
added1/1
computing V1
added1/1
computing diff
checked
n=1, N=2, r=1
n=1, N=2, r=1 already checked
n=1, N=2, r=2
n=1, N=2, r=2 already checked
n=1, N=2, r=3
n=1, N=2, r=3 already checked
n=1, N=2, r=4
computing S1
added1/2
added2/2
computing V1
added1/2
added2/2
computing diff
checked
n=1, N=3, r=1
n=1, N=3, r=1 already checked
n=1, N=3, r=2
n=1, N=3, r=2 already checked
n=1, N=3, r=3
n=1, N=3, r=3 already checked
n=1, N=3, r=4
computing S1
added1/3
added2/3
added3/3
computing V1
added1/3
added2/3
added3/3
computing diff
checked
n=1, N=4, r=1
computing S1
added1/4
added2/4
added3/4
added4/4
computing V1
added1/4
added2/4
added3/4
added4/4
computing diff
checked
n=1, N=4, r=2
computing S1
added1/4
added2/4
added3/4
added4/4
computing V1
added1/4
added2/4
added3/4
added4/4
computing diff
checked
n=1, N=4, r=3
computing S1
added1/4
a

In [10]:
SV_check_fast(1,10)

n=1, N=1, r=1
n=1, N=1, r=1 already checked
n=1, N=1, r=2
n=1, N=1, r=2 already checked
n=1, N=1, r=3
n=1, N=1, r=3 already checked
n=1, N=1, r=4
n=1, N=1, r=4 already checked
n=1, N=1, r=5
n=1, N=1, r=5 already checked
n=1, N=1, r=6
computing S1
added1/1
computing V1
added1/1
computing diff
checked
n=1, N=1, r=7
computing S1
added1/1
computing V1
added1/1
computing diff
checked
n=1, N=1, r=8
computing S1
added1/1
computing V1
added1/1
computing diff
checked
n=1, N=1, r=9
computing S1
added1/1
computing V1
added1/1
computing diff
checked
n=1, N=1, r=10
computing S1


IndexError: list index out of range

In [220]:
((prod(v[i] for i in range(1)))^1)

v1

In [ ]:
bernoulli_polynomial(1, 1)/factorial(k+1)

In [234]:
Z=fixed_locus(2,1)[1]
pretty(deg0(top_chern(-x1^5)*todd_class_fast(x1^5,5))).__str__()

'1/2'

In [232]:
todd_class_fast(x1^5,5)

-125/144*t1^5 + 125/36*t1^3 + 25/4*t1^2 + 5*t1 + 1

In [231]:
pretty(deg0(measure_unsymmetrized(x1^5)(x1=exp(t1),x2=exp(t2),x3=exp(t3),v1=exp(w1),v2=exp(w2),y1=exp(m1),y2=exp(m2)))).__str__()

'1/2'

In [195]:
deg0n(determinant_quot(Z,2,1)(x1=exp(t1),x2=exp(t2),x3=exp(t3),v1=exp(w1),v2=exp(w2),y1=exp(m1),y2=exp(m2)),4)

1/24*(2*m2 - t1 - t2 - t3 + 2*w1)^4

In [178]:
determinant(Q)

x1^-1*x2^-1*x3^-1*y3^2

In [155]:
pretty(deg0n(determinant_quot(fixed_locus(2,2)[2],1,1)(x1=exp(t1),x2=exp(t2),x3=exp(t3),v1=exp(w1),v2=exp(w2),y1=exp(m1),y2=exp(m2)),2)).__str__()

'1/2*(2*m2 + t1 + w1)^2'

In [156]:
pretty(determinant_quot_fast(fixed_locus(2,2)[2],1,1,2))

2*m2^2 + 2*m2*t1 + 1/2*t1^2 + 2*m2*w1 + t1*w1 + 2*m2 + t1 + w1 + 1

In [240]:
Verlinde_Num_quot_fast(2,1,1).__str__()

added1/4
added2/4
added3/4
added4/4


'(120*t1^4*t2^2*t3*m1 + 240*t1^3*t2^3*t3*m1 + 120*t1^2*t2^4*t3*m1 + 120*t1^4*t2*t3^2*m1 + 480*t1^3*t2^2*t3^2*m1 + 480*t1^2*t2^3*t3^2*m1 + 120*t1*t2^4*t3^2*m1 + 240*t1^3*t2*t3^3*m1 + 480*t1^2*t2^2*t3^3*m1 + 240*t1*t2^3*t3^3*m1 + 120*t1^2*t2*t3^4*m1 + 120*t1*t2^2*t3^4*m1 - 16*t1^4*t2^2*m1^2 - 32*t1^3*t2^3*m1^2 - 16*t1^2*t2^4*m1^2 - 32*t1^4*t2*t3*m1^2 - 96*t1^3*t2^2*t3*m1^2 - 96*t1^2*t2^3*t3*m1^2 - 32*t1*t2^4*t3*m1^2 - 16*t1^4*t3^2*m1^2 - 96*t1^3*t2*t3^2*m1^2 - 160*t1^2*t2^2*t3^2*m1^2 - 96*t1*t2^3*t3^2*m1^2 - 16*t2^4*t3^2*m1^2 - 32*t1^3*t3^3*m1^2 - 96*t1^2*t2*t3^3*m1^2 - 96*t1*t2^2*t3^3*m1^2 - 32*t2^3*t3^3*m1^2 - 16*t1^2*t3^4*m1^2 - 32*t1*t2*t3^4*m1^2 - 16*t2^2*t3^4*m1^2 + 120*t1^4*t2^2*t3*w1 + 240*t1^3*t2^3*t3*w1 + 120*t1^2*t2^4*t3*w1 + 120*t1^4*t2*t3^2*w1 + 480*t1^3*t2^2*t3^2*w1 + 480*t1^2*t2^3*t3^2*w1 + 120*t1*t2^4*t3^2*w1 + 240*t1^3*t2*t3^3*w1 + 480*t1^2*t2^2*t3^3*w1 + 240*t1*t2^3*t3^3*w1 + 120*t1^2*t2*t3^4*w1 + 120*t1*t2^2*t3^4*w1 - 32*t1^4*t2^2*m1*w1 - 64*t1^3*t2^3*m1*w1 - 32*t1^2*t2^4*m1*w1 - 64*t1^4*t2*t3*m1*w1 - 192*t1^3*t2^2*t3*m1*w1 - 192*t1^2*t2^3*t3*m1*w1 - 64*t1*t2^4*t3*m1*w1 - 32*t1^4*t3^2*m1*w1 - 192*t1^3*t2*t3^2*m1*w1 - 320*t1^2*t2^2*t3^2*m1*w1 - 192*t1*t2^3*t3^2*m1*w1 - 32*t2^4*t3^2*m1*w1 - 64*t1^3*t3^3*m1*w1 - 192*t1^2*t2*t3^3*m1*w1 - 192*t1*t2^2*t3^3*m1*w1 - 64*t2^3*t3^3*m1*w1 - 32*t1^2*t3^4*m1*w1 - 64*t1*t2*t3^4*m1*w1 - 32*t2^2*t3^4*m1*w1 - 16*t1^4*t2^2*w1^2 - 32*t1^3*t2^3*w1^2 - 16*t1^2*t2^4*w1^2 - 32*t1^4*t2*t3*w1^2 - 96*t1^3*t2^2*t3*w1^2 - 96*t1^2*t2^3*t3*w1^2 - 32*t1*t2^4*t3*w1^2 - 16*t1^4*t3^2*w1^2 - 96*t1^3*t2*t3^2*w1^2 - 160*t1^2*t2^2*t3^2*w1^2 - 96*t1*t2^3*t3^2*w1^2 - 16*t2^4*t3^2*w1^2 - 32*t1^3*t3^3*w1^2 - 96*t1^2*t2*t3^3*w1^2 - 96*t1*t2^2*t3^3*w1^2 - 32*t2^3*t3^3*w1^2 - 16*t1^2*t3^4*w1^2 - 32*t1*t2*t3^4*w1^2 - 16*t2^2*t3^4*w1^2)/(-16*t1^4*t2^2*t3^2 - 32*t1^3*t2^3*t3^2 - 16*t1^2*t2^4*t3^2 - 32*t1^3*t2^2*t3^3 - 32*t1^2*t2^3*t3^3 - 16*t1^2*t2^2*t3^4)'

In [238]:
pretty(deg0(Verlinde_Num_quot(2,1,1)(x1=exp(t1),x2=exp(t2),x3=exp(t3),v1=exp(w1),v2=exp(w2),y1=exp(m1),y2=exp(m2)))).__str__()

added1/4
added2/4
added3/4
added4/4


'1/2*(2*m1*t1^2*t2 + 2*m1*t1*t2^2 + 2*m1*t1^2*t3 + 4*m1*t1*t2*t3 - 15*t1^2*t2*t3 + 2*m1*t2^2*t3 - 15*t1*t2^2*t3 + 2*m1*t1*t3^2 + 2*m1*t2*t3^2 - 15*t1*t2*t3^2 + 2*t1^2*t2*w1 + 2*t1*t2^2*w1 + 2*t1^2*t3*w1 + 4*t1*t2*t3*w1 + 2*t2^2*t3*w1 + 2*t1*t3^2*w1 + 2*t2*t3^2*w1)*(m1 + w1)*(t1 + t2)*(t1 + t3)*(t2 + t3)/((t1 + t2 + t3)^2*t1^2*t2^2*t3^2)'

In [108]:
pretty(Verlinde_Num_quot_fast(1,1,2)).__str__()

added1/1


'(2*m1 + w1 + w2)*(t1 + t2)*(t1 + t3)*(t2 + t3)/((t1 + t2 + t3)*t1*t2*t3)'

In [109]:
pretty(deg0(Verlinde_Num_quot(1,1,2)(x1=exp(t1),x2=exp(t2),x3=exp(t3),v1=exp(w1),v2=exp(w2),y1=exp(m1)))).__str__()

added1/1


'(2*m1 + w1 + w2)*(t1 + t2)*(t1 + t3)*(t2 + t3)/((t1 + t2 + t3)*t1*t2*t3)'

In [79]:
set_exp(x1+x2,5)

1/120*t1^5 + 1/120*t2^5 + 1/24*t1^4 + 1/24*t2^4 + 1/6*t1^3 + 1/6*t2^3 + 1/2*t1^2 + 1/2*t2^2 + t1 + t2 + 2

In [125]:
pretty(Segre_Num_quot_fast(1,2,1)).__str__()

added1/2
added2/2


'(m1 + m2 + 2*w1)*(t1 + t2)*(t1 + t3)*(t2 + t3)/((t1 + t2 + t3)*t1*t2*t3)'

In [126]:
pretty(deg0(Segre_Num_quot(1,2,1))).__str__()

added1/2
added2/2


'(m1 + m2 + 2*w1)*(t1 + t2)*(t1 + t3)*(t2 + t3)/((t1 + t2 + t3)*t1*t2*t3)'

In [49]:
total_segre_quot_fast(fixed_locus(2,1)[1],1,2)

t1^2 + 2*t1*t2 + t2^2 + 2*t1*t3 + 2*t2*t3 + t3^2 - 3*t1*m1 - 3*t2*m1 - 3*t3*m1 + 3*m1^2 - 3*t1*w1 - 3*t2*w1 - 3*t3*w1 + 6*m1*w1 + 3*w1^2 + t1 + t2 + t3 - 2*m1 - 2*w1 + 1

In [18]:
S1=Segre_Num_quot(2,1,2)
S2=Segre_Num_quot(2,2,1)
diff=S1*(-1)^(2*1)-symmetrize(S2)*(-1)^(2*2)
diff

added1/4
added2/4
added3/4
added4/4
added1/9
added2/9
added3/9
added4/9
added5/9
added6/9
added7/9
added8/9
added9/9


0

In [9]:
S1.

(-8*t1^8*t2^4 - 32*t1^7*t2^5 - 48*t1^6*t2^6 - 32*t1^5*t2^7 - 8*t1^4*t2^8 - 32*t1^8*t2^3*t3 - 160*t1^7*t2^4*t3 - 320*t1^6*t2^5*t3 - 320*t1^5*t2^6*t3 - 160*t1^4*t2^7*t3 - 32*t1^3*t2^8*t3 - 48*t1^8*t2^2*t3^2 - 320*t1^7*t2^3*t3^2 - 848*t1^6*t2^4*t3^2 - 1152*t1^5*t2^5*t3^2 - 848*t1^4*t2^6*t3^2 - 320*t1^3*t2^7*t3^2 - 48*t1^2*t2^8*t3^2 - 32*t1^8*t2*t3^3 - 320*t1^7*t2^2*t3^3 - 1152*t1^6*t2^3*t3^3 - 2080*t1^5*t2^4*t3^3 - 2080*t1^4*t2^5*t3^3 - 1152*t1^3*t2^6*t3^3 - 320*t1^2*t2^7*t3^3 - 32*t1*t2^8*t3^3 - 8*t1^8*t3^4 - 160*t1^7*t2*t3^4 - 848*t1^6*t2^2*t3^4 - 2080*t1^5*t2^3*t3^4 - 2768*t1^4*t2^4*t3^4 - 2080*t1^3*t2^5*t3^4 - 848*t1^2*t2^6*t3^4 - 160*t1*t2^7*t3^4 - 8*t2^8*t3^4 - 32*t1^7*t3^5 - 320*t1^6*t2*t3^5 - 1152*t1^5*t2^2*t3^5 - 2080*t1^4*t2^3*t3^5 - 2080*t1^3*t2^4*t3^5 - 1152*t1^2*t2^5*t3^5 - 320*t1*t2^6*t3^5 - 32*t2^7*t3^5 - 48*t1^6*t3^6 - 320*t1^5*t2*t3^6 - 848*t1^4*t2^2*t3^6 - 1152*t1^3*t2^3*t3^6 - 848*t1^2*t2^4*t3^6 - 320*t1*t2^5*t3^6 - 48*t2^6*t3^6 - 32*t1^5*t3^7 - 160*t1^4*t2*t3^7 - 320*t1^3*t2^2*t3^7 - 320*t1^2*t2^3*t3^7 - 160*t1*t2^4*t3^7 - 32*t2^5*t3^7 - 8*t1^4*t3^8 - 32*t1^3*t2*t3^8 - 48*t1^2*t2^2*t3^8 - 32*t1*t2^3*t3^8 - 8*t2^4*t3^8 - 16*t1^8*t2^3*m1 - 64*t1^7*t2^4*m1 - 112*t1^6*t2^5*m1 - 112*t1^5*t2^6*m1 - 64*t1^4*t2^7*m1 - 16*t1^3*t2^8*m1 - 64*t1^8*t2^2*t3*m1 - 320*t1^7*t2^3*t3*m1 - 720*t1^6*t2^4*t3*m1 - 928*t1^5*t2^5*t3*m1 - 720*t1^4*t2^6*t3*m1 - 320*t1^3*t2^7*t3*m1 - 64*t1^2*t2^8*t3*m1 - 64*t1^8*t2*t3^2*m1 - 512*t1^7*t2^2*t3^2*m1 - 1664*t1^6*t2^3*t3^2*m1 - 2896*t1^5*t2^4*t3^2*m1 - 2896*t1^4*t2^5*t3^2*m1 - 1664*t1^3*t2^6*t3^2*m1 - 512*t1^2*t2^7*t3^2*m1 - 64*t1*t2^8*t3^2*m1 - 16*t1^8*t3^3*m1 - 320*t1^7*t2*t3^3*m1 - 1664*t1^6*t2^2*t3^3*m1 - 4160*t1^5*t2^3*t3^3*m1 - 5600*t1^4*t2^4*t3^3*m1 - 4160*t1^3*t2^5*t3^3*m1 - 1664*t1^2*t2^6*t3^3*m1 - 320*t1*t2^7*t3^3*m1 - 16*t2^8*t3^3*m1 - 64*t1^7*t3^4*m1 - 720*t1^6*t2*t3^4*m1 - 2896*t1^5*t2^2*t3^4*m1 - 5600*t1^4*t2^3*t3^4*m1 - 5600*t1^3*t2^4*t3^4*m1 - 2896*t1^2*t2^5*t3^4*m1 - 720*t1*t2^6*t3^4*m1 - 64*t2^7*t3^4*m1 - 112*t1^6*t3^5*m1 - 928*t1^5*t2*t3^5*m1 - 2896*t1^4*t2^2*t3^5*m1 - 4160*t1^3*t2^3*t3^5*m1 - 2896*t1^2*t2^4*t3^5*m1 - 928*t1*t2^5*t3^5*m1 - 112*t2^6*t3^5*m1 - 112*t1^5*t3^6*m1 - 720*t1^4*t2*t3^6*m1 - 1664*t1^3*t2^2*t3^6*m1 - 1664*t1^2*t2^3*t3^6*m1 - 720*t1*t2^4*t3^6*m1 - 112*t2^5*t3^6*m1 - 64*t1^4*t3^7*m1 - 320*t1^3*t2*t3^7*m1 - 512*t1^2*t2^2*t3^7*m1 - 320*t1*t2^3*t3^7*m1 - 64*t2^4*t3^7*m1 - 16*t1^3*t3^8*m1 - 64*t1^2*t2*t3^8*m1 - 64*t1*t2^2*t3^8*m1 - 16*t2^3*t3^8*m1 - 8*t1^8*t2^2*m1^2 - 32*t1^7*t2^3*m1^2 - 64*t1^6*t2^4*m1^2 - 80*t1^5*t2^5*m1^2 - 64*t1^4*t2^6*m1^2 - 32*t1^3*t2^7*m1^2 - 8*t1^2*t2^8*m1^2 - 16*t1^8*t2*t3*m1^2 - 96*t1^7*t2^2*t3*m1^2 - 320*t1^6*t2^3*t3*m1^2 - 592*t1^5*t2^4*t3*m1^2 - 592*t1^4*t2^5*t3*m1^2 - 320*t1^3*t2^6*t3*m1^2 - 96*t1^2*t2^7*t3*m1^2 - 16*t1*t2^8*t3*m1^2 - 8*t1^8*t3^2*m1^2 - 96*t1^7*t2*t3^2*m1^2 - 512*t1^6*t2^2*t3^2*m1^2 - 1376*t1^5*t2^3*t3^2*m1^2 - 1904*t1^4*t2^4*t3^2*m1^2 - 1376*t1^3*t2^5*t3^2*m1^2 - 512*t1^2*t2^6*t3^2*m1^2 - 96*t1*t2^7*t3^2*m1^2 - 8*t2^8*t3^2*m1^2 - 32*t1^7*t3^3*m1^2 - 320*t1^6*t2*t3^3*m1^2 - 1376*t1^5*t2^2*t3^3*m1^2 - 2752*t1^4*t2^3*t3^3*m1^2 - 2752*t1^3*t2^4*t3^3*m1^2 - 1376*t1^2*t2^5*t3^3*m1^2 - 320*t1*t2^6*t3^3*m1^2 - 32*t2^7*t3^3*m1^2 - 64*t1^6*t3^4*m1^2 - 592*t1^5*t2*t3^4*m1^2 - 1904*t1^4*t2^2*t3^4*m1^2 - 2752*t1^3*t2^3*t3^4*m1^2 - 1904*t1^2*t2^4*t3^4*m1^2 - 592*t1*t2^5*t3^4*m1^2 - 64*t2^6*t3^4*m1^2 - 80*t1^5*t3^5*m1^2 - 592*t1^4*t2*t3^5*m1^2 - 1376*t1^3*t2^2*t3^5*m1^2 - 1376*t1^2*t2^3*t3^5*m1^2 - 592*t1*t2^4*t3^5*m1^2 - 80*t2^5*t3^5*m1^2 - 64*t1^4*t3^6*m1^2 - 320*t1^3*t2*t3^6*m1^2 - 512*t1^2*t2^2*t3^6*m1^2 - 320*t1*t2^3*t3^6*m1^2 - 64*t2^4*t3^6*m1^2 - 32*t1^3*t3^7*m1^2 - 96*t1^2*t2*t3^7*m1^2 - 96*t1*t2^2*t3^7*m1^2 - 32*t2^3*t3^7*m1^2 - 8*t1^2*t3^8*m1^2 - 16*t1*t2*t3^8*m1^2 - 8*t2^2*t3^8*m1^2 + 16*t1^6*t2^3*m1^3 + 48*t1^5*t2^4*m1^3 + 48*t1^4*t2^5*m1^3 + 16*t1^3*t2^6*m1^3 + 80*t1^6*t2^2*t3*m1^3 + 288*t1^5*t2^3*t3*m1^3 + 416*t1^4*t2^4*t3*m1^3 + 288*t1^3*t2^5*t3*m1^3 + 80*t1^2*t2^6*t3*m1^3 + 80*t1^6*t2*t3^2*m1^3 + 480*t1^5*t2

In [19]:
V1=Verlinde_Num_quot(2,1,2)
V2=Verlinde_Num_quot(2,2,1)
diff=deg0(set_exp(V1-symmetrizeK(V2)))
check1=false
check2=false
check3=false
if diff.numerator()==0:
    check1=true
    check2=true
    check3=true
else:
    for f,e in diff.numerator().factor_list():
        if e>=2:
            if f==t1+t2:
                check1=true
            if f==t2+t3:
                check2=true
            if f==t1+t3:
                check3=true
                
print(check1)
print(check2)
print(check3)
diff

added1/4
added2/4
added3/4
added4/4
added1/9
added2/9
added3/9
added4/9
added5/9
added6/9
added7/9
added8/9
added9/9
True
True
True


-1/2*(t1 + t2)^2*(t1 + t3)^2*(t2 + t3)^2*(w1 - w2)^2/((t1 + t2 + t3)^2*t1^2*t2^2*t3^2)

In [3]:
S1=Segre_Num_quot(2,1,2)
V1=Verlinde_Num_quot(2,1,2)
Sp=deg0(S1)
Vp=deg0(set_exp(V1))
diff= Sp-(-1)^(1*2)*Vp
print(diff)
check1=false
check2=false
check3=false
if diff.numerator()==0:
    check1=true
    check2=true
    check3=true
else:
    for f,e in diff.numerator().factor_list():
        if e>=2:
            if f==t1+t2:
                check1=true
            if f==t2+t3:
                check2=true
            if f==t1+t3:
                check3=true
if check1 and check2 and check3:
    print("checked")


added1/4
added2/4
added3/4
added4/4
added1/4
added2/4
added3/4
added4/4


TypeError: ECL says: Console interrupt.

In [29]:
S1=Segre_Num_quot(2,1,2)
D1=pretty(S1(t1=b*t1,t2=b*t2,t3=b*t3,t4=b*t4,
                         m1=b*m1,m2=b*m2,m3=b*m3,m4=b*m4,m5=b*m5,
                         w1=b*w1,w2=b*w2,w3=b*w3,w4=b*w4,w5=b*w5)*b^2)

added1/4
added2/4
added3/4
added4/4


In [32]:
D1=pretty(S1(t1=b*t1,t2=b*t2,t3=b*t3,t4=b*t4,
                         m1=b*m1,m2=b*m2,m3=b*m3,m4=b*m4,m5=b*m5,
                         w1=b*w1,w2=b*w2,w3=b*w3,w4=b*w4,w5=b*w5)*b^2)
str(D1)

'1/2*(b^6*m1^6*t1^2*t2 - 2*b^6*m1^4*t1^4*t2 + b^6*m1^2*t1^6*t2 + b^6*m1^6*t1*t2^2 - 4*b^6*m1^4*t1^3*t2^2 - 2*b^6*m1^3*t1^4*t2^2 + 3*b^6*m1^2*t1^5*t2^2 + 2*b^6*m1*t1^6*t2^2 - 4*b^6*m1^4*t1^2*t2^3 - 4*b^6*m1^3*t1^3*t2^3 + 5*b^6*m1^2*t1^4*t2^3 + 6*b^6*m1*t1^5*t2^3 + b^6*t1^6*t2^3 - 2*b^6*m1^4*t1*t2^4 - 2*b^6*m1^3*t1^2*t2^4 + 5*b^6*m1^2*t1^3*t2^4 + 8*b^6*m1*t1^4*t2^4 + 3*b^6*t1^5*t2^4 + 3*b^6*m1^2*t1^2*t2^5 + 6*b^6*m1*t1^3*t2^5 + 3*b^6*t1^4*t2^5 + b^6*m1^2*t1*t2^6 + 2*b^6*m1*t1^2*t2^6 + b^6*t1^3*t2^6 + b^6*m1^6*t1^2*t3 - 2*b^6*m1^4*t1^4*t3 + b^6*m1^2*t1^6*t3 + 2*b^6*m1^6*t1*t2*t3 + 10*b^6*m1^5*t1^2*t2*t3 - 8*b^6*m1^4*t1^3*t2*t3 - 8*b^6*m1^3*t1^4*t2*t3 + 6*b^6*m1^2*t1^5*t2*t3 + 6*b^6*m1*t1^6*t2*t3 + b^6*m1^6*t2^2*t3 + 10*b^6*m1^5*t1*t2^2*t3 - 12*b^6*m1^4*t1^2*t2^2*t3 - 20*b^6*m1^3*t1^3*t2^2*t3 + 22*b^6*m1^2*t1^4*t2^2*t3 + 24*b^6*m1*t1^5*t2^2*t3 + 3*b^6*t1^6*t2^2*t3 - 8*b^6*m1^4*t1*t2^3*t3 - 20*b^6*m1^3*t1^2*t2^3*t3 + 34*b^6*m1^2*t1^3*t2^3*t3 + 44*b^6*m1*t1^4*t2^3*t3 + 12*b^6*t1^5*t2^3*t3 - 2*b^6*m1^4*t2^4*t3 - 8*b^6*m1^3*t1*t2^4*t3 + 22*b^6*m1^2*t1^2*t2^4*t3 + 44*b^6*m1*t1^3*t2^4*t3 + 18*b^6*t1^4*t2^4*t3 + 6*b^6*m1^2*t1*t2^5*t3 + 24*b^6*m1*t1^2*t2^5*t3 + 12*b^6*t1^3*t2^5*t3 + b^6*m1^2*t2^6*t3 + 6*b^6*m1*t1*t2^6*t3 + 3*b^6*t1^2*t2^6*t3 + b^6*m1^6*t1*t3^2 - 4*b^6*m1^4*t1^3*t3^2 - 2*b^6*m1^3*t1^4*t3^2 + 3*b^6*m1^2*t1^5*t3^2 + 2*b^6*m1*t1^6*t3^2 + b^6*m1^6*t2*t3^2 + 10*b^6*m1^5*t1*t2*t3^2 - 12*b^6*m1^4*t1^2*t2*t3^2 - 20*b^6*m1^3*t1^3*t2*t3^2 + 22*b^6*m1^2*t1^4*t2*t3^2 + 24*b^6*m1*t1^5*t2*t3^2 + 3*b^6*t1^6*t2*t3^2 - 12*b^6*m1^4*t1*t2^2*t3^2 - 32*b^6*m1^3*t1^2*t2^2*t3^2 + 58*b^6*m1^2*t1^3*t2^2*t3^2 + 78*b^6*m1*t1^4*t2^2*t3^2 + 18*b^6*t1^5*t2^2*t3^2 - 4*b^6*m1^4*t2^3*t3^2 - 20*b^6*m1^3*t1*t2^3*t3^2 + 58*b^6*m1^2*t1^2*t2^3*t3^2 + 114*b^6*m1*t1^3*t2^3*t3^2 + 39*b^6*t1^4*t2^3*t3^2 - 2*b^6*m1^3*t2^4*t3^2 + 22*b^6*m1^2*t1*t2^4*t3^2 + 78*b^6*m1*t1^2*t2^4*t3^2 + 39*b^6*t1^3*t2^4*t3^2 + 3*b^6*m1^2*t2^5*t3^2 + 24*b^6*m1*t1*t2^5*t3^2 + 18*b^6*t1^2*t2^5*t3^2 + 2*b^6*m1*t2^6*t3^2 + 3*b^6*t1*t2^6*t3^2 - 4*b^6*m1^4*t1^2*t3^3 - 4*b^6*m1^3*t1^3*t3^3 + 5*b^6*m1^2*t1^4*t3^3 + 6*b^6*m1*t1^5*t3^3 + b^6*t1^6*t3^3 - 8*b^6*m1^4*t1*t2*t3^3 - 20*b^6*m1^3*t1^2*t2*t3^3 + 34*b^6*m1^2*t1^3*t2*t3^3 + 44*b^6*m1*t1^4*t2*t3^3 + 12*b^6*t1^5*t2*t3^3 - 4*b^6*m1^4*t2^2*t3^3 - 20*b^6*m1^3*t1*t2^2*t3^3 + 58*b^6*m1^2*t1^2*t2^2*t3^3 + 114*b^6*m1*t1^3*t2^2*t3^3 + 39*b^6*t1^4*t2^2*t3^3 - 4*b^6*m1^3*t2^3*t3^3 + 34*b^6*m1^2*t1*t2^3*t3^3 + 114*b^6*m1*t1^2*t2^3*t3^3 + 56*b^6*t1^3*t2^3*t3^3 + 5*b^6*m1^2*t2^4*t3^3 + 44*b^6*m1*t1*t2^4*t3^3 + 39*b^6*t1^2*t2^4*t3^3 + 6*b^6*m1*t2^5*t3^3 + 12*b^6*t1*t2^5*t3^3 + b^6*t2^6*t3^3 - 2*b^6*m1^4*t1*t3^4 - 2*b^6*m1^3*t1^2*t3^4 + 5*b^6*m1^2*t1^3*t3^4 + 8*b^6*m1*t1^4*t3^4 + 3*b^6*t1^5*t3^4 - 2*b^6*m1^4*t2*t3^4 - 8*b^6*m1^3*t1*t2*t3^4 + 22*b^6*m1^2*t1^2*t2*t3^4 + 44*b^6*m1*t1^3*t2*t3^4 + 18*b^6*t1^4*t2*t3^4 - 2*b^6*m1^3*t2^2*t3^4 + 22*b^6*m1^2*t1*t2^2*t3^4 + 78*b^6*m1*t1^2*t2^2*t3^4 + 39*b^6*t1^3*t2^2*t3^4 + 5*b^6*m1^2*t2^3*t3^4 + 44*b^6*m1*t1*t2^3*t3^4 + 39*b^6*t1^2*t2^3*t3^4 + 8*b^6*m1*t2^4*t3^4 + 18*b^6*t1*t2^4*t3^4 + 3*b^6*t2^5*t3^4 + 3*b^6*m1^2*t1^2*t3^5 + 6*b^6*m1*t1^3*t3^5 + 3*b^6*t1^4*t3^5 + 6*b^6*m1^2*t1*t2*t3^5 + 24*b^6*m1*t1^2*t2*t3^5 + 12*b^6*t1^3*t2*t3^5 + 3*b^6*m1^2*t2^2*t3^5 + 24*b^6*m1*t1*t2^2*t3^5 + 18*b^6*t1^2*t2^2*t3^5 + 6*b^6*m1*t2^3*t3^5 + 12*b^6*t1*t2^3*t3^5 + 3*b^6*t2^4*t3^5 + b^6*m1^2*t1*t3^6 + 2*b^6*m1*t1^2*t3^6 + b^6*t1^3*t3^6 + b^6*m1^2*t2*t3^6 + 6*b^6*m1*t1*t2*t3^6 + 3*b^6*t1^2*t2*t3^6 + 2*b^6*m1*t2^2*t3^6 + 3*b^6*t1*t2^2*t3^6 + b^6*t2^3*t3^6 + 3*b^6*m1^5*t1^2*t2*w1 - 4*b^6*m1^3*t1^4*t2*w1 + b^6*m1*t1^6*t2*w1 + 3*b^6*m1^5*t1*t2^2*w1 - 8*b^6*m1^3*t1^3*t2^2*w1 - 3*b^6*m1^2*t1^4*t2^2*w1 + 3*b^6*m1*t1^5*t2^2*w1 + b^6*t1^6*t2^2*w1 - 8*b^6*m1^3*t1^2*t2^3*w1 - 6*b^6*m1^2*t1^3*t2^3*w1 + 5*b^6*m1*t1^4*t2^3*w1 + 3*b^6*t1^5*t2^3*w1 - 4*b^6*m1^3*t1*t2^4*w1 - 3*b^6*m1^2*t1^2*t2^4*w1 + 5*b^6*m1*t1^3*t2^4*w1 + 4*b^6*t1^4*t2^4*w1 + 3*b^6*m1*t1^2*t2^5*w1 + 3*b^6*t1^3*t2^5*w1 + b^6*m1*t1*t2^6*w1 + b^6*t1^2*t2^6*w1 + 3*b^6*m1^5*t1^2*t3*w1 - 4*b

In [30]:
derivative(b^9,b,8)

362880*b

In [25]:
(S1*b).parent()

Symbolic Ring

In [23]:
((b^9+1)/b^8).coefficient(b^8)

0

In [109]:
B=Segre_Num_quot(2,2,1)(w1=m1,w2=m2,w3=m3,w4=m4,m1=w1,m2=w2,m3=w3,m4=w4)


In [110]:
(A-B).__str__()

'0'

In [ ]:
A=Segre_Num_quot(2,2,2)
B=A(w1=m1,w2=m2,m1=w1,m2=w2)
(A-B).__str__()

In [ ]:
G=Segre_Num_quot(3,2,1)
H=Segre_Num_quot(3,1,2)(w1=m1,m1=w1,m2=w2)
I=G+H
I

In [216]:
deg0(Segre_Num_quot(2,2,1))

1/2*(3*m1^2*t1^2*t2 + 4*m1*m2*t1^2*t2 + 3*m2^2*t1^2*t2 + 3*m1^2*t1*t2^2 + 4*m1*m2*t1*t2^2 + 3*m2^2*t1*t2^2 + 3*m1^2*t1^2*t3 + 4*m1*m2*t1^2*t3 + 3*m2^2*t1^2*t3 + 6*m1^2*t1*t2*t3 + 8*m1*m2*t1*t2*t3 + 6*m2^2*t1*t2*t3 - 25*m1*t1^2*t2*t3 - 25*m2*t1^2*t2*t3 + 3*m1^2*t2^2*t3 + 4*m1*m2*t2^2*t3 + 3*m2^2*t2^2*t3 - 25*m1*t1*t2^2*t3 - 25*m2*t1*t2^2*t3 + 3*m1^2*t1*t3^2 + 4*m1*m2*t1*t3^2 + 3*m2^2*t1*t3^2 + 3*m1^2*t2*t3^2 + 4*m1*m2*t2*t3^2 + 3*m2^2*t2*t3^2 - 25*m1*t1*t2*t3^2 - 25*m2*t1*t2*t3^2 + 10*m1*t1^2*t2*w1 + 10*m2*t1^2*t2*w1 + 10*m1*t1*t2^2*w1 + 10*m2*t1*t2^2*w1 + 10*m1*t1^2*t3*w1 + 10*m2*t1^2*t3*w1 + 20*m1*t1*t2*t3*w1 + 20*m2*t1*t2*t3*w1 - 50*t1^2*t2*t3*w1 + 10*m1*t2^2*t3*w1 + 10*m2*t2^2*t3*w1 - 50*t1*t2^2*t3*w1 + 10*m1*t1*t3^2*w1 + 10*m2*t1*t3^2*w1 + 10*m1*t2*t3^2*w1 + 10*m2*t2*t3^2*w1 - 50*t1*t2*t3^2*w1 + 10*t1^2*t2*w1^2 + 10*t1*t2^2*w1^2 + 10*t1^2*t3*w1^2 + 20*t1*t2*t3*w1^2 + 10*t2^2*t3*w1^2 + 10*t1*t3^2*w1^2 + 10*t2*t3^2*w1^2)*(t1 + t2)*(t1 + t3)*(t2 + t3)/((t1 + t2 + t3)^2*t1^2*t2^2*t3^2)

In [221]:
pretty(Segre_Num_quot(1,2,1))

(m1 + m2 + 2*w1)*(t1 + t2)*(t1 + t3)*(t2 + t3)/((t1 + t2 + t3)*t1*t2*t3)

In [172]:
pretty(Verlinde_Num_quot_inv(2,3))

0

Observation: The symmetry holds for Segre number withour restricting degrees, and without the $c_3(X)^2$ condition. But for Verlinde number, we need to restrict to degree 0, and the difference is again only a multiple of $c_3(X)^2$. We also the fact that Cao-Kool conjecture says universal series for rank $-1$ Segre (restricting degree) agrees with the compact case. So we might suspect that in general the Segre series restricted to degree 0 agrees with compact case without the $c_3(X)^2$ condition. BUT this does not hold for surface case (fails for rank $+1$), so it might be a coincidence for rank $-1$, or a special property for 4-folds.

In [142]:
pretty(Chern_Num_quot(1,4,3))

(t1 + t2)*(t1 + t3)*(t2 + t3)/((t1 + t2 + t3)*t1*t2*t3)